# H3 Python API

In [4]:
from h3 import h3
import folium

def visualize_hexagons(hexagons, color="red", folium_map=None):
    """
    hexagons is a list of hexcluster. Each hexcluster is a list of hexagons. 
    eg. [[hex1, hex2], [hex3, hex4]]
    """
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        # flatten polygons into loops.
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    
    if folium_map is None:
        m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    else:
        m = folium_map
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
        m.add_child(my_PolyLine)
    return m
    

def visualize_polygon(polyline, color):
    polyline.append(polyline[0])
    lat = [p[0] for p in polyline]
    lng = [p[1] for p in polyline]
    m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
    m.add_child(my_PolyLine)
    return m

In [22]:
def find_cells_for_geojson(geojson, level):
    cells = h3.polyfill(geojson, level, geo_json_conformant=True)
    if len(cells):
        return cells, level
    increased_level = level + 1
    return find_cell_for_geojson(geojson, increased_level)
    


In [3]:
h3_address = h3.geo_to_h3(37.3615593, -122.0553238, 9) # lat, lng, hex resolution                                                                                                        
m = visualize_hexagons([h3_address])
display(m)

In [6]:
list(h3.k_ring_distances(h3_address, 4))

[{'89283470d93ffff'},
 {'89283470d83ffff',
  '89283470d97ffff',
  '89283470d9bffff',
  '89283472b2bffff',
  '89283472b2fffff',
  '89283472b67ffff'},
 {'89283470d87ffff',
  '89283470d8bffff',
  '89283470d8fffff',
  '89283470dd7ffff',
  '89283472b23ffff',
  '89283472b27ffff',
  '89283472b3bffff',
  '89283472b63ffff',
  '89283472b6fffff',
  '89283472b77ffff',
  '8928347764bffff',
  '8928347765bffff'},
 {'89283470d13ffff',
  '89283470d17ffff',
  '89283470db3ffff',
  '89283470dbbffff',
  '89283470dc3ffff',
  '89283470dc7ffff',
  '89283470dd3ffff',
  '89283472b07ffff',
  '89283472b0fffff',
  '89283472b33ffff',
  '89283472b37ffff',
  '89283472b6bffff',
  '89283472b73ffff',
  '89283472b7bffff',
  '89283477643ffff',
  '8928347764fffff',
  '89283477653ffff',
  '892834776cbffff'},
 {'89283470ca7ffff',
  '89283470cb7ffff',
  '89283470d03ffff',
  '89283470d07ffff',
  '89283470d1bffff',
  '89283470da3ffff',
  '89283470dabffff',
  '89283470db7ffff',
  '89283470dcbffff',
  '89283470dcfffff',
  '892834

In [15]:
h3_address = h3.geo_to_h3(37.3615593, -122.0553238, 9) # lat, lng, hex resolution                                                                                                        
h3_address = h3.h3_to_parent('89b91695833ffff', 8)

hex_center_coordinates = h3.h3_to_geo(h3_address) # array of [lat, lng]                                                                                                                  
hex_boundary = h3.h3_to_geo_boundary(h3_address) # array of arrays of [lat, lng]                                                                                                                                                                                                                                                         
m = visualize_hexagons(list(h3.k_ring_distances(h3_address, 4)[3]), color="purple")
m = visualize_hexagons(list(h3.k_ring_distances(h3_address, 4)[2]), color="blue", folium_map=m)
m = visualize_hexagons(list(h3.k_ring_distances(h3_address, 4)[1]), color="green", folium_map=m)
m = visualize_hexagons(list(h3.k_ring_distances(h3_address, 4)[0]), color = "red", folium_map=m)
display(m)



In [2]:
import requests
# get the data from the server
url = "https://gist.githubusercontent.com/sabman/f1aee8de222c263fb0aa4d40409404e7/raw/118150c1d402d5a998a5b180731a98ac33983dad/jettyroad.geojson"

r = requests.get(url)
data = r.json()
geoJson = data['features'][0]['geometry']

In [28]:
# print(geoJson)
polyline = geoJson['coordinates'][0]
# reverse the coordinates to be [lat, lng]
polyline = list(map(lambda v: [v[1], v[0]], polyline))
polyline.append(polyline[0])
lat = [p[0] for p in polyline]
lng = [p[1] for p in polyline]
m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color="green")
m.add_child(my_PolyLine)
# polyfill function g
# 6 => check if polyfill returns a list of hexagons
# 7 => check if polyfill returns a list of hexagons
# 8 => check if polyfill returns a list of hexagons
# 9 => check if polyfill returns a list of hexagons
# loop until we find a hexagon who's centroid is inside the polygon
# then find the parent of the found hexagon cell and return the parent at level 6


# hexagons = list(h3.polyfill(geoJson, 9, geo_json_conformant=True))            

found_hexagons, level = find_cells_for_geojson(geoJson, 6)
print(found_hexagons, level)
hexagons = []
if level > 6:
    # get get parents of these at 6
    for h in found_hexagons:
        hexagons.append(h3.h3_to_parent(h, 6))

polylines = []
lat = []
lng = []
for hex in hexagons:
    polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
    # flatten polygons into loops.
    outlines = [loop for polygon in polygons for loop in polygon]
    polyline = [outline + [outline[0]] for outline in outlines][0]
    lat.extend(map(lambda v:v[0],polyline))
    lng.extend(map(lambda v:v[1],polyline))
    polylines.append(polyline)
for polyline in polylines:
    my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color='red')
    m.add_child(my_PolyLine)
display(m)


{'8eb916958372897', '8eb9169583367b7', '8eb9169583725b7', '8eb916958041967', '8eb91695830620f', '8eb916958372037', '8eb916958072b4f', '8eb916958046167', '8eb91695830daf7', '8eb91695830ca5f', '8eb9169583044b7', '8eb916958046107', '8eb916958306b6f', '8eb916958041077', '8eb91695807392f', '8eb91695833676f', '8eb91695804c14f', '8eb916958040327', '8eb91695837270f', '8eb91695830ccaf', '8eb916958332837', '8eb916958041b17', '8eb916958301aef', '8eb916958070617', '8eb91695830619f', '8eb91695830cc2f', '8eb91695807604f', '8eb916958040157', '8eb91695804dd17', '8eb91695830c9a7', '8eb91695830626f', '8eb916958076257', '8eb91695807291f', '8eb9169580452c7', '8eb91695804d1af', '8eb916958076217', '8eb916958040c5f', '8eb9169583723b7', '8eb9169580739b7', '8eb916958072827', '8eb9169583307af', '8eb91695830680f', '8eb916958076487', '8eb916958040ce7', '8eb91695833066f', '8eb91695833060f', '8eb91695830db17', '8eb916958333377', '8eb91695830d837', '8eb91695804d04f', '8eb91695807071f', '8eb916958044257', '8eb9169580

In [8]:
geoJson = {'type': 'Polygon',
 'coordinates': [[[37.813318999983238, -122.4089866999972145], [ 37.7866302000007224, -122.3805436999997056 ], [37.7198061999978478, -122.3544736999993603], [ 37.7076131999975672, -122.5123436999983966 ], [37.7835871999971715, -122.5247187000021967],  [37.8151571999998453, -122.4798767000009008]]] }

polyline = geoJson['coordinates'][0]
polyline.append(polyline[0])
lat = [p[0] for p in polyline]
lng = [p[1] for p in polyline]
m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color="green")
m.add_child(my_PolyLine)
# polyfill function g
hexagons = list(h3.polyfill(geoJson, 8))
polylines = []
lat = []
lng = []
for hex in hexagons:
    polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
    # flatten polygons into loops.
    outlines = [loop for polygon in polygons for loop in polygon]
    polyline = [outline + [outline[0]] for outline in outlines][0]
    lat.extend(map(lambda v:v[0],polyline))
    lng.extend(map(lambda v:v[1],polyline))
    polylines.append(polyline)
for polyline in polylines:
    my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color='red')
    m.add_child(my_PolyLine)
display(m)